<div style="border: 2px solid #8A9AD0; margin: 1em 0.2em; padding: 0.5em;">

# Predicting Mutation Impact with Zero-shot Learning using a pretrained DNA LLM

by [Raphael Mourad](https://training.galaxyproject.org/hall-of-fame/raphaelmourad/), [Bérénice Batut](https://training.galaxyproject.org/hall-of-fame/bebatut/)

CC-BY licensed content from the [Galaxy Training Network](https://training.galaxyproject.org/)

**Objectives**

- How does zero-shot learning differ from traditional supervised learning, and what advantages does it offer in the context of predicting DNA mutation impacts?
- What steps are involved in computing embeddings for DNA sequences using a pre-trained LLM, and how do these embeddings capture the semantic meaning of the sequences?
- Why is the L2 distance used as a metric to quantify the impact of mutations, and how does a higher L2 distance indicate a more significant mutation effect?

**Objectives**

- Explain the concept of zero-shot learning and its application in predicting the impact of DNA mutations using pre-trained large language models (LLMs).
- Utilize a pre-trained DNA LLM from Hugging Face to compute embeddings for wild-type and mutated DNA sequences.
- Compare the embeddings of wild-type and mutated sequences to quantify the impact of mutations using L2 distance as a metric.
- Interpret the results of the L2 distance calculations to determine the significance of mutation effects and discuss potential implications in genomics research.
- Develop a script to automate the process of predicting mutation impacts using zero-shot learning, enabling researchers to apply this method to their own datasets efficiently.

**Time Estimation: 3H**
</div>


<p>Predicting the impact of mutations is a critical task in genomics, as it provides insights into how genetic variations influence biological functions and contribute to diseases. Traditional methods for assessing mutation impact often rely on extensive experimental data or computationally intensive simulations. However, with the advent of large language models (LLMs) and zero-shot learning, we can now predict mutation impacts more efficiently and effectively.</p>
<p>Zero-shot learning is a technique that allows a pre-trained model to make predictions on tasks it wasn’t explicitly trained for, leveraging its existing knowledge. This approach is particularly valuable when labeled data is scarce or when rapid predictions are needed. By using a pre-trained DNA LLM, we can compute embeddings for both wild-type and mutated DNA sequences and compare them to quantify the impact of mutations.</p>
<p>This tutorial focuses on this innovative method, utilizing a <a href="https://huggingface.co/RaphaelMourad/Mistral-DNA-v1-17M-hg38">pre-trained DNA LLM available on Hugging Face</a> to assess the impact of mutations. This approach opens new avenues for bioinformatics research, particularly in genomics and personalized medicine, by enabling researchers to gain insights into the functional impact of DNA mutations efficiently.</p>
<p>Building upon this foundation, our new tutorial focuses on predicting the impact of mutations using zero-shot learning with a pre-trained DNA LLM. Zero-shot learning allows us to utilize the pre-trained model directly, without additional training, to make predictions on new, unseen tasks. Specifically, we will use a pre-trained model available on Hugging Face, designed for DNA sequences, to assess the impact of mutations.</p>
<p>We will use <a href="https://huggingface.co/RaphaelMourad/Mistral-DNA-v1-1M-hg38"><code class="language-plaintext highlighter-rouge">Mistral-DNA-v1-17M-hg38</code></a>, a mixed model that was pre-trained on the entire Human Genome. It contains approximately 17 million parameters and was trained using the Human Genome assembly GRCh38 on sequences of 10,000 bases (10K):</p>


In [ ]:
model_name="RaphaelMourad/Mistral-DNA-v1-17M-hg38"

<blockquote class="agenda" style="border: 2px solid #86D486;display: none; margin: 1em 0.2em">
<div class="box-title agenda-title" id="agenda">Agenda</div>
<p>In this tutorial, we will cover:</p>
<ol id="markdown-toc">
<li><a href="#prepare-resources" id="markdown-toc-prepare-resources">Prepare resources</a>    <ol>
<li><a href="#install-dependencies" id="markdown-toc-install-dependencies">Install dependencies</a></li>
</ol>
</li>
</ol>
</blockquote>
<h1 id="prepare-resources">Prepare resources</h1>
<h2 id="install-dependencies">Install dependencies</h2>
<p>The first step is to install the required dependencies:</p>


In [ ]:
!pip install Bio==1.7.1
!pip install transformers -U

<h2 id="import-python-libraries">Import Python libraries</h2>
<p>Let’s now import them.</p>


In [ ]:
import os

import matplotlib.pyplot as plt
import numpy as np
import scipy as sp
import torch
import tensorflow as tf
import gzip
from Bio import SeqIO
from transformers import (
  AutoConfig,
  AutoModelForCausalLM,
  AutoTokenizer,
  EarlyStoppingCallback,
  Trainer,
  TrainingArguments,
)

<blockquote class="comment" style="border: 2px solid #ffecc1; margin: 1em 0.2em">
<div class="box-title comment-title" id="comment-versions"><i class="far fa-comment-dots" aria-hidden="true" ></i> Comment: Versions</div>
<p>This tutorial has been tested with following versions:</p>
<ul>
<li><code style="color: inherit">transformers</code> = 4.48.3</li>
</ul>
<p>You can check the versions with:</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit">transformers.__version__
</code></pre></div>  </div>
</blockquote>
<h2 id="check-and-configure-available-resources">Check and configure available resources</h2>
<p>We select the appropriate device (CUDA-enabled GPU if available) for running PyTorch operations</p>


In [ ]:
torch.device('cuda' if torch.cuda.is_available() else 'cpu')

<p>Let’s check the GPU usage and RAM:</p>


In [ ]:
!nvidia-smi

<p>Let’s configure PyTorch and the CUDA environment – software and hardware ecosystem provided by NVIDIA to enable parallel computing on GPU – to optimize GPU memory usage and performance:</p>
<ol>
<li>
<p>Enables CuDNN benchmarking in PyTorch:</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit"> torch.backends.cudnn.benchmark=True
</code></pre></div>    </div>
</li>
<li>
<p>Set an environment variable that configures how PyTorch manages CUDA memory allocations</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit"> os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "max_split_size_mb:32"
</code></pre></div>    </div>
</li>
</ol>
<h1 id="tokenizing-dna-sequences">Tokenizing DNA Sequences</h1>
<p>We now set up the tokenizer to convert raw DNA sequences into a format that the model can process, enabling it to understand and analyze the sequences effectively:</p>


In [ ]:
tokenizer = transformers.AutoTokenizer.from_pretrained(
    model_name,
    use_fast=True,
    trust_remote_code=True,
)

<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<p>What do the parameters?</p>
<ol>
<li><code style="color: inherit">use_fast=True</code>?</li>
<li><code style="color: inherit">trust_remote_code=True</code>?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution"><button class="gtn-boxify-button solution" type="button" aria-controls="solution" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<ol>
<li><code style="color: inherit">use_fast=True</code>: Enables the use of a fast tokenizer implementation, which is optimized for speed and efficiency. This is particularly useful when working with large datasets or when performance is a priority.</li>
<li><code style="color: inherit">trust_remote_code=True</code>: Allows the tokenizer to execute custom code from the model repository. This may be necessary for certain architectures or preprocessing steps that require additional functionality.</li>
</ol>
</details>
</blockquote>
<h1 id="load-and-configure-the-pre-trained-model">Load and Configure the Pre-trained Model</h1>
<p>We will now load the pre-trained DNA large language model (LLM) and configure it for our specific task of predicting the impact of DNA mutations.</p>


In [ ]:
model=transformers.AutoModelForCausalLM.from_pretrained(
    model_name,
)

<p>We would like to ensure that the model correctly handles padding tokens, which are used to standardize the length of sequences within a batch:</p>


In [ ]:
model.config.pad_token_id = tokenizer.pad_token_id

<p>Aligning the padding token ID between the model and tokenizer is crucial for maintaining consistency during training and inference.</p>
<p>Let’s look at the model:</p>


In [ ]:
model

<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit">MixtralForCausalLM(
  (model): MixtralModel(
    (embed_tokens): Embedding(4096, 256)
    (layers): ModuleList(
      (0-7): 8 x MixtralDecoderLayer(
        (self_attn): MixtralAttention(
          (q_proj): Linear(in_features=256, out_features=256, bias=False)
          (k_proj): Linear(in_features=256, out_features=256, bias=False)
          (v_proj): Linear(in_features=256, out_features=256, bias=False)
          (o_proj): Linear(in_features=256, out_features=256, bias=False)
        )
        (block_sparse_moe): MixtralSparseMoeBlock(
          (gate): Linear(in_features=256, out_features=8, bias=False)
          (experts): ModuleList(
            (0-7): 8 x MixtralBlockSparseTop2MLP(
              (w1): Linear(in_features=256, out_features=256, bias=False)
              (w2): Linear(in_features=256, out_features=256, bias=False)
              (w3): Linear(in_features=256, out_features=256, bias=False)
              (act_fn): SiLU()
            )
          )
        )
        (input_layernorm): MixtralRMSNorm((256,), eps=1e-05)
        (post_attention_layernorm): MixtralRMSNorm((256,), eps=1e-05)
      )
    )
    (norm): MixtralRMSNorm((256,), eps=1e-05)
    (rotary_emb): MixtralRotaryEmbedding()
  )
  (lm_head): Linear(in_features=256, out_features=4096, bias=False)
)
</code></pre></div></div>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-1"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<p>What do the parameters?</p>
<ol>
<li>How does the vocabulary size of 4,096 relate to k-mers in DNA sequences?</li>
<li>What is the role of the embedding layer in <code style="color: inherit">MixtralForCausalLM</code>?</li>
<li>How many layers does the <code style="color: inherit">MixtralForCausalLM</code> model have, and what is their purpose?</li>
<li>What components make up the self-attention mechanism in MixtralAttention?</li>
<li>How does the Mixture of Experts (MoE) mechanism reduce computational load?</li>
<li>Why is layer normalization important in <code style="color: inherit">MixtralForCausalLM</code>?</li>
<li>What advantage do rotary embeddings offer in understanding DNA sequences?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-1"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-1" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<ol>
<li>The vocabulary size corresponds to the number of unique “words” or k-mers (subsequences of DNA) the model can recognize, similar to using k-mers of size six, enhanced by byte-pair encoding for more nuanced patterns.</li>
<li>The embedding layer converts DNA sequences into numerical vectors, enabling the model to process and analyze them.</li>
<li>The model has 8 layers, each containing a <code style="color: inherit">MixtralDecoderLayer</code>. These layers process the embedded input sequences through a series of transformations, including self-attention and mixture of experts, to capture complex patterns in the data.</li>
<li>The self-attention mechanism includes query, key, value, and output projections, which weigh the importance of different tokens in the sequence.</li>
<li>MoE activates only a subset of parameters during each forward pass, using a routing mechanism to direct sequences to specific experts.</li>
<li>Layer normalization stabilizes and accelerates training by ensuring consistent scaling of inputs to the attention mechanism and subsequent layers.</li>
<li>Rotary embeddings enhance the model’s understanding of positional information, providing a more nuanced representation of sequence order compared to traditional methods.</li>
</ol>
</details>
</blockquote>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-2"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<p>For a DNA sequence “ACGTAGCATCGGATCTATCTATCGACACTTGGTTATCGATCTACGAGCATCTCGTTAGC”</p>
<ol>
<li>How can we get the hidden states?</li>
<li>How can we compute mean of the hidden states accross the sequence length dimension?</li>
<li>What is the shape of the output?</li>
<li>What does the mean of the hidden states accross the sequence length dimension represent?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-2"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-2" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>Let’s start by defining the DNA sequence:</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit">dna = "ACGTAGCATCGGATCTATCTATCGACACTTGGTTATCGATCTACGAGCATCTCGTTAGC"
</code></pre></div>    </div>
<ol>
<li>To get the hidden state:
<ol>
<li>
<p>Tokenize the DNA sequence using the tokenizer</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit"> tokenized_dna = tokenizer(dna, return_tensors = "pt")
</code></pre></div>            </div>
</li>
<li>
<p>Extract the tensor containing the token IDs from the tokenized output</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit"> inputs = tokenized_dna["input_ids"]
</code></pre></div>            </div>
</li>
<li>
<p>Pass the tokenized input through the model.</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit"> model_outputs = model(inputs)
</code></pre></div>            </div>
</li>
<li>
<p>Extract the hidden states from the model’s output.</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit"> hidden_states = model_outputs[0].detach()
</code></pre></div>            </div>
</li>
</ol>
</li>
<li>
<p>To compute mean of the hidden states accross the sequence length dimension:</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit">embedding_mean = torch.mean(hidden_states[0], dim=0)
</code></pre></div>        </div>
</li>
<li>
<p>The shape is 4,096, the number of possible tokens</p>
</li>
<li>It represents the average embedding of the DNA sequence. This fixed-size representation can be used for various downstream tasks, such as classification, clustering, or similarity comparisons.</li>
</ol>
</blockquote>
</blockquote>
<h1 id="compare-the-effect-of-mutations-with-or-without-amino-acid-modification">Compare the effect of mutations with or without amino acid modification</h1>
<p>Let’s look at the portion of the Cystic fibrosis transmembrane conductance regulator (CFTR) gene where a mutation responsible of the Cystic fibrosis appears.</p>
<p>In this portion, we can observe several cases:</p>
<table>
<thead>
<tr>
<th>Cases</th>
<th>Sequences</th>
</tr>
</thead>
<tbody>
<tr>
<td>Wild-type without any mutation</td>
<td>ATTAAAGAAAATATCATCTTTGGTGTTTCCTAT</td>
</tr>
<tr>
<td>Mutation ATT to ATA</td>
<td>ATAAAAGAAAATATCATCTTTGGTGTTTCCTAT</td>
</tr>
<tr>
<td>Deletion of TCT codon</td>
<td>ATTAAAGAAAATATCA—TTGGTGTTTCCTAT</td>
</tr>
</tbody>
</table>
<p>In the second case, the amino acid does not change (silent mutation). In the last case, an amino acid is removed. Let’s look if the mutation and the deletion have the same distance to the wild-type when computing using the DNA embedding.</p>
<p>First, we define the sequences:</p>


In [ ]:
dna_wt= "ATTAAAGAAAATATCATCTTTGGTGTTTCCTAT"
dna_mut="ATAAAAGAAAATATCATCTTTGGTGTTTCCTAT"
dna_del="ATTAAAGAAAATATCATTGGTGTTTCCTAT"

<p>Let’s compute the hidden states for all DNA sequences:</p>


In [ ]:
tokenized_dna = tokenizer(
  [dna_wt, dna_mut, dna_del],
  return_tensors="pt",
  padding=True,
)
inputs_seqs = tokenized_dna["input_ids"]
model_outputs = model(inputs_seqs)
hidden_states = model_outputs.detach()

<p>We now compute the maximum of the hidden states accross the sequence length dimension:</p>


In [ ]:
embedding_max = torch.max(hidden_states, dim=1)[0]

<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-3"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-3"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-3" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
</details>
</blockquote>
<p>To compare the effects of silent mutation and amino acid deletion, we will compute the distance between the wild-type embeddings and the mutation / deletion embedding using the L2 (Euclidian) distance</p>
<blockquote class="details" style="border: 2px solid #ddd; margin: 1em 0.2em">
<div class="box-title details-title" id="details-l2-euclidian-distance"><button class="gtn-boxify-button details" type="button" aria-controls="details-l2-euclidian-distance" aria-expanded="true"><i class="fas fa-info-circle" aria-hidden="true" ></i> <span>Details: L2 (Euclidian) distance</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>The L2 distance, also known as the Euclidean distance, is a measure of the straight-line distance between two points in Euclidean space. It is commonly used to quantify the difference between two vectors, such as embeddings in machine learning.</p>
<p>For two vectors \(a\) and \(b\) in an \(n\)-dimensional space, where \(a=[a\_{1},a\_{2},...,a\_{n}]\) and \(b=[b\_{1},b\_{2},...,b\_{n}]\), the L2 distance is calculated as:</p>
<p>\( L2 = \sqrt{\sum_{i} (a_{i}-b_{i})^{2} \)</p>
</blockquote>


In [ ]:
wt_mut_L2 = torch.norm(embedding_max[0] - embedding_max[1])
print(wt_mut_L2)
wt_del_L2 = torch.norm(embedding_max[0] - embedding_max[2])
print(wt_del_L2)

<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit">tensor(27.4657)
tensor(145.7797)
</code></pre></div></div>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-4"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<ol>
<li>Is it the silent mutation or the amino acid deletion that have the lowest L2 distance to the wild-type?</li>
<li>How to interpret the result?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-4"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-4" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<ol>
<li>The silent mutation has a lower L2 distance to the wild-type compared to the mutation with amino acid deletion.</li>
<li>A smaller L2 distance indicates that the sequences are more similar, while a larger distance suggests greater dissimilarity.</li>
</ol>
</details>
</blockquote>
<h1 id="compare-effects-of-snps-in-exons-and-introns">Compare effects of SNPs in exons and introns</h1>
<p>Single Nucleotide Polymorphisms (SNPs) are the most common type of genetic variation, involving a change in a single nucleotide within a DNA sequence. These variations can occur in different regions of the genome, including exons (the coding regions of genes) and introns (the non-coding regions within genes). Understanding the impact of SNPs in these regions is crucial for assessing their role in genetic disorders, phenotypic traits, and overall genome function.</p>
<p>We will now leverage the pre-trained DNA language model to compare the effects of SNPs in exons and introns. By utilizing embeddings generated from DNA sequences, we can quantify the impact of these variations and gain insights into their functional consequences.</p>
<h2 id="load-sequences">Load sequences</h2>
<p>To begin our analysis, we need to load the sequence data, which includes sequences with Single Nucleotide Polymorphisms (SNPs) and their corresponding reference sequences (wild-type) without SNPs. These sequences are derived from both introns and exons and are stored in compressed FASTA format on <a href="https://github.com/raphaelmourad/Mistral-DNA/tree/main/data/SNP">GitHub</a>:</p>
<table>
<thead>
<tr>
<th>Wild-type (without SNPs)</th>
<th>Mutated (with SNP)</th>
<th> </th>
</tr>
</thead>
<tbody>
<tr>
<td>Intron</td>
<td><a href="https://github.com/raphaelmourad/Mistral-DNA/raw/refs/head/master/data/SNP/SNPintron_ref_201b.fasta.gz"><code class="language-plaintext highlighter-rouge">SNPintron_ref_201b.fasta.gz</code></a></td>
<td><a href="https://github.com/raphaelmourad/Mistral-DNA/raw/refs/head/master/data/SNP/SNPintron_alt_201b.fasta.gz"><code class="language-plaintext highlighter-rouge">SNPintron_alt_201b.fasta.gz</code></a></td>
</tr>
<tr>
<td>Exon</td>
<td><a href="https://github.com/raphaelmourad/Mistral-DNA/raw/refs/head/master/data/SNP/SNPexon_ref_201b.fasta.gz"><code class="language-plaintext highlighter-rouge">SNPexon_ref_201b.fasta.gz</code></a></td>
<td><a href="https://github.com/raphaelmourad/Mistral-DNA/raw/refs/head/master/data/SNP/SNPexon_alt_201b.fasta.gz"><code class="language-plaintext highlighter-rouge">SNPexon_alt_201b.fasta.gz</code></a></td>
</tr>
</tbody>
</table>


In [ ]:
baseurl = "https://github.com/raphaelmourad/Mistral-DNA/raw/refs/head/master/data/SNP/"
win=201
exon_wt_snp_fp = f"{ baseurl }/SNPexon_ref_{ win }b.fasta.gz"
exon_mut_snp_fp = f"{ baseurl }/SNPexon_alt_ { win }b.fasta.gz"
intron_wf_snp_fp = f"{ baseurl }/SNPintron_ref_ { win }b.fasta.gz"
intron_mut_snp_fp = f"{ baseurl }/SNPintron_alt_ { win }b.fasta.gz"

<p>We need to get files and read the sequences from them:</p>


In [ ]:
def downloadReadFastaFile(fasta_file):
  response = requests.get(url)
  # Check if the request was successful
  if response.status_code == 200:
      # Open a local file in binary write mode and save the content
      with open('file.gz', 'wb') as file:
          file.write(response.content)
      print("File downloaded successfully.")
  else:
      print(f"Failed to download file. HTTP Status code: {response.status_code}")
  # Read the file
  seql_list=[]
  with gzip.open(fasta_file, "rt") as handle:
      for record in SeqIO.parse(handle, "fasta"):
          seqj=str(record.seq)
          seql_list.append(seqj)
  return seql_list

exon_wt_seqs = readRegularFastaFile(exon_wt_snp_fp)
exon_mut_seqs = readRegularFastaFile(exon_mut_snp_fp)
intron_wt_seqs = readRegularFastaFile(intron_wt_snp_fp)
intron_mut_seqs = readRegularFastaFile(intron_mut_snp_fp)

<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-5"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<ol>
<li>How many sequences are in the data?</li>
<li>How are the sequences?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-5"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-5" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>1.
2.</p>
</details>
</blockquote>
<p>We will keep only the 100 first sequences:</p>


In [ ]:
kseq = 100
exon_wt_seqs = exon_wt_seqs[0:kseq]
exon_mut_seqs = exon_mut_seqs[0:kseq]
intron_wt_seqs = intron_wt_seqs[0:kseq]
intron_mut_seqs = intron_mut_seqs[0:kseq]

<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-6"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<p>How many differences (SNPs) between reference and alternative sequences are there for first exon sequence?</p>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-6"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-6" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
</details>
</blockquote>
<h2 id="compute-effect-of-snps">Compute effect of SNPs</h2>
<p>To compute the effect of SNPs, we need :</p>
<ol>
<li>Compute the embdedding of DNA sequences</li>
</ol>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit">  def computeEmbedding(seqs):
    tokenized_dna = tokenizer(
      seqs,
      return_tensors="pt",
      padding=True,
    )
    inputs_seqs = tokenized_dna["input_ids"]
    hidden_states = model(inputs_seqs)[0].detach().cpu().numpy()
    return torch.max(hidden_states, dim=1)
</code></pre></div></div>
<ol>
<li>Compute the L2 distance between reference (without SNP) and alternative (with SNP):</li>
</ol>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit">  def computeMutationEffect(wt_seqs, mut_seqs):
    wt_embedding = computeEmbedding(wt_seqs)
    mut_embedding = computeEmbedding(mut_seqs)
    return torch.norm(mut_embedding - wt_embedding)
</code></pre></div></div>


In [ ]:
exon_SNP_distL2 = computeMutationEffect(exon_wt_seqs, exon_mut_seqs)
intron_SNP_distL2 = computeMutationEffect(intron_wt_seqs,intron_mut_seqs)

<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-7"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<p>What are the dimensions of <code style="color: inherit">exon_SNP_distL2</code> and <code style="color: inherit">intron_SNP_distL2</code>?</p>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-7"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-7" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
</details>
</blockquote>
<h2 id="compare-snps-effects-between-introns-and-exons">Compare SNPs effects between introns and exons</h2>
<p>We can now quantify the impact of SNPs and determine if the differences are statistically significant.</p>
<p>To visualize the predicted effects of SNPs, we can use a boxplot to compare the L2 distances for SNPs in exons and introns. The L2 distance serves as a metric for the impact of mutations, with higher distances indicating a more significant effect.</p>
<p>Boxplot of predicted SNP effects</p>


In [ ]:
SNPs_distL2 = {"exons": exon_SNP_distL2, "introns": intron_SNP_distL2}

fig, ax = plt.subplots()
ax.boxplot(SNPs_distL2.values())
ax.set_xticklabels(SNPs_distL2.keys())

<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-8"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<p><a href="./images/boxplot.png" rel="noopener noreferrer"><img src="./images/boxplot.png" alt="Box plot comparing two categories: exonSNPs and intronSNPs. The plot displays the distribution of values for each category, with the median indicated by an orange line within each box. The boxes represent the interquartile range, while the whiskers extend to show the range of the data, excluding outliers, which are depicted as individual points above the whiskers. The exonSNPs category shows a higher median and more variability compared to the intronSNPs category." width="543" height="413" loading="lazy" /></a></p>
<p>What can we conclude from the boxplot?</p>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-8"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-8" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>From the plot, we observe that the L2 distance is generally higher for SNPs in exons compared to those in introns. This suggests that SNPs in exons have a stronger predicted effect, which aligns with their role in coding regions of genes.</p>
</details>
</blockquote>
<p>To determine if the observed differences in L2 distances are statistically significant, we can perform hypothesis tests to compare the distributions:</p>
<ul>
<li>
<p>T-test:</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit">sp.stats.ttest_ind(exon_SNP_distL2, intron_SNP_distL2)
</code></pre></div>    </div>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-9"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<p>What can we conclude from the t-test?</p>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-9"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-9" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>The t-test yields a p-value of approximately \(7.56 \cdot 10^{−7}\), indicating a statistically significant difference between the L2 distances of SNPs in exons and introns.</p>
</blockquote>
</blockquote>
</li>
<li>
<p>Wilcoxon rank-sum test:</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit">sp.stats.wilcoxon(distL2_exonSNPs,distL2_intronSNPs)
</code></pre></div>    </div>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-10"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<p>What can we conclude from the Wilcoxon test?</p>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-10"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-10" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>The Wilcoxon rank-sum test also shows a significant p-value of approximately \(2.87 \cdot 10^{−6}\), confirming that the distributions are significantly different.</p>
</blockquote>
</blockquote>
</li>
</ul>
<p>The analysis demonstrates that SNPs in exons have a more substantial impact on the sequence embeddings compared to SNPs in introns, as evidenced by higher L2 distances. This finding is statistically significant, highlighting the importance of exonic SNPs in potentially altering gene function and expression. By understanding these differences, researchers can gain insights into the functional consequences of genetic variations in different genomic regions.</p>
<h1 id="conclusion">Conclusion</h1>
<p>Throughout this tutorial, we explored a comprehensive workflow for analyzing DNA sequences and assessing the impact of mutations using a pre-trained DNA language model. We began by tokenizing DNA sequences, converting them into numerical representations that the model could process and analyze effectively. Following this, we loaded and configured a pre-trained model to handle these sequences, ensuring seamless integration with the tokenizer. We then delved into comparing the effects of mutations, both with and without amino acid modifications, showcasing the model’s ability to discern subtle differences in sequence impacts. Furthermore, we focused on analyzing the effects of Single Nucleotide Polymorphisms (SNPs) in exons and introns. By loading the relevant sequences, computing the L2 distances between embeddings of wild-type and mutated sequences, and visualizing the results, we quantified and compared the impact of SNPs in these regions. Our analysis revealed that SNPs in exons generally have a more significant impact than those in introns, a finding supported by statistical tests. This tutorial underscores the power of pre-trained models in bioinformatics, offering valuable insights into the functional consequences of genetic variations and paving the way for further research in genomics.</p>


# Key Points

- Pre-trained DNA language models are powerful tools for analyzing genetic sequences, enabling efficient and accurate assessment of mutation impacts without extensive computational resources.
- SNPs in exons generally have a more significant impact on gene function compared to those in introns, highlighting the importance of focusing on coding regions for understanding genetic variations.
- Utilizing embeddings to quantify the effects of mutations provides a robust method for comparing sequence variations, offering insights into the functional consequences of SNPs and other genetic modifications.
- Employing statistical tests, such as t-tests and Wilcoxon rank-sum tests, is crucial for validating observed differences in genetic data, ensuring that findings are supported by empirical evidence.

# Congratulations on successfully completing this tutorial!

Please [fill out the feedback on the GTN website](https://training.galaxyproject.org/training-material/topics/statistics/tutorials/genomic-llm-zeroshot-prediction/tutorial.html#feedback) and check there for further resources!
